# LangChain QA Panel App

This notebook shows how to make this app:

In [ ]:
# !pip install transformers
# !pip install easyocr
# !pip install pdf2image
# !apt-get install poppler-utils


Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/
Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/
Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/
Reading package lists... Done
Building dependency tree       
Reading state information... Done
poppler-utils is already the newest version (0.86.1-0ubuntu1.1).
0 upgraded, 0 newly installed, 0 to remove and 38 not upgraded.


In [ ]:
import panel as pn
from transformers import pipeline
from pdf2image import convert_from_path
import easyocr

In [ ]:
pn.extension('texteditor', template="bootstrap", sizing_mode='stretch_width')
pn.state.template.param.update(
    main_max_width="690px",
    header_background="#F08080",
)

In [ ]:
file_input = pn.widgets.FileInput(width=300)

prompt = pn.widgets.TextEditor(
    value="", placeholder="Enter your questions here...", height=160, toolbar=False
)
run_button = pn.widgets.Button(name="Run")

widgets = pn.Row(
    pn.Column(prompt, run_button, margin=5), width = 630
)

In [ ]:
def qa(file, query):

    images = convert_from_path(file)
    reader = easyocr.Reader(['en'])
    result = []
    for i in range(len(images)):
      # Save pages as images in the pdf
      images[i].save('page'+ str(i) +'.jpg', 'JPEG')
      x=str(i)
      t='page'+x+'.jpg'
      result.append(reader.readtext(t, detail = 0))
    text = ""
    for page in result:
      page_text = " ".join(page)
      text += page_text
    model =  pipeline("question-answering", model='deepset/roberta-base-squad2')
    context = text
    result = model(question=query, context=context)
    print(f"Answer: {result['answer']}")
    return result

In [ ]:
convos = []  # list of all panel objects

def qa_result(_):
    # saving pdf as a temp file
    if file_input.value is not None:
        file_input.save("/.cache/temp.pdf")

        prompt_text = prompt.value
        if prompt_text:
            result = qa(file="/.cache/temp.pdf", query=prompt_text)
            convos.extend([
                pn.Row(
                    pn.panel("Q: ", width=10),
                    prompt_text,
                    width=600
                ),
                pn.Row(
                    pn.panel("A: ", width=10),
                    pn.Column(
                        result["answer"],
                    )
                )
            ])
            #return convos
    return pn.Column(*convos, margin=15, width=575, min_height=400)


In [ ]:
qa_interactive = pn.panel(
    pn.bind(qa_result, run_button),
    loading_indicator=True,
)

In [ ]:
output = pn.WidgetBox('*Output will show up here:*', qa_interactive, width=630, scroll=True)

In [ ]:
# layout
pn.Column(
    pn.pane.Markdown("""
    Question Answering with your PDF file!

    1) Upload a PDF. \n
    2) Type a question and click "Run".

    """),
    pn.Row(file_input),
    output,
    widgets

).servable()

Answer: 40 
Answer: Production, and Editing

Column(sizing_mode='stretch_width')
    [0] Markdown(str, sizing_mode='stretch_width')
    [1] Row(sizing_mode='stretch_width')
        [0] FileInput(width=300)
    [2] WidgetBox(scroll=True, width=630)
        [0] Markdown(str, sizing_mode='stretch_width')
        [1] ParamFunction(function, _pane=Column, loading_indicator=True, sizing_mode='stretch_width')
    [3] Row(width=630)
        [0] Column(margin=5, sizing_mode='stretch_width')
            [0] TextEditor(height=160, placeholder='Enter your questions h..., sizing_mode='stretch_width', toolbar=False)
            [1] Button(name='Run', sizing_mode='stretch_width')